In [117]:
import pandas as pd
import numpy as np

### Сначала ищем ошибки в исходном Датасете airport_raw

In [118]:
patch = 'https://raw.githubusercontent.com/jpatokal/openflights/master/data/airports.dat'
airport_raw = pd.read_csv(patch, sep = ',', engine = 'python',
           header = None,
           names = ['Airport ID', 'Name', 'City', 'Country', 'IATA', 'ICAO', 'Latitude', 'Longitude', 'Altitude', 'Timezone', 'DST', 'Tz database time zone', 'Type', 'Source'])
airport_raw.head()

Airport ID                                         Name          City  \
0           1                               Goroka Airport        Goroka   
1           2                               Madang Airport        Madang   
2           3                 Mount Hagen Kagamuga Airport   Mount Hagen   
3           4                               Nadzab Airport        Nadzab   
4           5  Port Moresby Jacksons International Airport  Port Moresby   

            Country IATA  ICAO  Latitude   Longitude  Altitude Timezone DST  \
0  Papua New Guinea  GKA  AYGA -6.081690  145.391998      5282       10   U   
1  Papua New Guinea  MAG  AYMD -5.207080  145.789001        20       10   U   
2  Papua New Guinea  HGU  AYMH -5.826790  144.296005      5388       10   U   
3  Papua New Guinea  LAE  AYNZ -6.569803  146.725977       239       10   U   
4  Papua New Guinea  POM  AYPY -9.443380  147.220001       146       10   U   

  Tz database time zone     Type       Source  
0  Pacific/Port_Moresby  airport  OurAirports  
1  Pacific/Port_Moresby  airport  OurAirports  
2  Pacific/Port_Moresby  airport  OurAirports  
3  Pacific/Port_Moresby  airport  OurAirports  
4  Pacific/Port_Moresby  airport  OurAirports

#### Пропущенные данные

На сайте по ссылке https://openflights.org/data.html в описании столбцов данных столбцов для датасета Airport database указано, что DST принимает одно из значений: E,A,S,O,Z,N,U где U-означает неизвестно. Но на самом деле при проверке оказывается, что в столбце DST также есть значения '\N'. Ниже я вывел такие строчки.

In [119]:
invalid_dst = airport_raw[~airport_raw['DST'].isin(['E', 'A', 'S', 'O', 'Z', 'N', 'U'])]
if len(invalid_dst) > 0:
    display(pd.DataFrame(invalid_dst))
else:
    print("Всё хорошо")

Airport ID                                           Name         City  \
6981       11743                            La Grande-4 Airport  La Grande-4   
6982       11744                              Alert Bay Airport    Alert Bay   
6983       11745         Liverpool South Shore Regional Airport    Liverpool   
6984       11747                                Nipawin Airport      Nipawin   
6985       11748  Centralia / James T. Field Memorial Aerodrome    Centralia   
...          ...                                            ...          ...   
7693       14106                            Rogachyovo Air Base       Belaya   
7694       14107                          Ulan-Ude East Airport     Ulan Ude   
7695       14108                           Krechevitsy Air Base     Novgorod   
7696       14109                    Desierto de Atacama Airport      Copiapo   
7697       14110                             Melitopol Air Base    Melitopol   

      Country IATA  ICAO   Latitude   Longitude  Altitude Timezone DST  \
6981   Canada  YAH  CYAH  53.754700  -73.675301      1005       \N  \N   
6982   Canada  YAL  CYAL  50.582199 -126.916000       240       \N  \N   
6983   Canada   \N  CYAU  44.230301  -64.856102       321       \N  \N   
6984   Canada   \N  CYBU  53.332500 -104.008003      1220       \N  \N   
6985   Canada  YCE  CYCE  43.285599  -81.508301       824       \N  \N   
...       ...  ...   ...        ...         ...       ...      ...  ..   
7693   Russia   \N  ULDA  71.616699   52.478298       272       \N  \N   
7694   Russia   \N  XIUW  51.849998  107.737999      1670       \N  \N   
7695   Russia   \N  ULLK  58.625000   31.385000        85       \N  \N   
7696    Chile  CPO  SCAT -27.261200  -70.779198       670       \N  \N   
7697  Ukraine   \N  UKDM  46.880001   35.305000         0       \N  \N   

     Tz database time zone     Type       Source  
6981                    \N  airport  OurAirports  
6982                    \N  airport  OurAirports  
6983                    \N  airport  OurAirports  
6984                    \N  airport  OurAirports  
6985                    \N  airport  OurAirports  
...                    ...      ...          ...  
7693                    \N  airport  OurAirports  
7694                    \N  airport  OurAirports  
7695                    \N  airport  OurAirports  
7696                    \N  airport  OurAirports  
7697                    \N  airport  OurAirports  

[353 rows x 14 columns]

В описании датасета не сказано, что данные в столбце City могут отсутствовать. Однако такие строки есть.

In [120]:
empty_city = airport_raw[airport_raw['City'].isnull()]
if len(empty_city) > 0:
    display(pd.DataFrame(empty_city))
else:
    print("Нет строк, удовлетворяющих условию")

Airport ID                                Name City       Country IATA  \
7031       11794  Minsk Mazowiecki Military Air Base  NaN        Poland   \N   
7032       11795            Powidz Military Air Base  NaN        Poland   \N   
7137       11900       King Salman Abdulaziz Airport  NaN  Saudi Arabia  DWD   
7138       11901                King Khaled Air Base  NaN  Saudi Arabia  KMX   
7158       11921                  Asahikawa Airfield  NaN         Japan   \N   
7160       11923                  Utsunomiya Airport  NaN         Japan   \N   
7161       11924    Jungwon Air Base/Chungju Airport  NaN   South Korea   \N   
7164       11927                      Bislig Airport  NaN   Philippines  BPH   
7165       11928               Mati National Airport  NaN   Philippines  MXI   
7184       11947               Metropolitano Airport  NaN     Venezuela   \N   
7191       11954                 Belaya Gora Airport  NaN        Russia  BGN   
7221       11984                  Volgodonsk Airport  NaN        Russia  VLK   
7233       11996                   Ratnagiri Airport  NaN         India  RTC   
7236       11999            Ambala Air Force Station  NaN         India   \N   
7237       12000             Sirsa Air Force Station  NaN         India   \N   
7238       12001          Udhampur Air Force Station  NaN         India   \N   
7249       12012                      Ararat Airport  NaN     Australia  ARY   
7250       12013                     Benalla Airport  NaN     Australia  BLN   
7251       12014                   Balranald Airport  NaN     Australia  BZD   
7252       12015                  Brewarrina Airport  NaN     Australia  BWQ   
7253       12016                       Cleve Airport  NaN     Australia  CVC   
7254       12017                      Corowa Airport  NaN     Australia  CWW   
7255       12018                    Corryong Airport  NaN     Australia  CYG   
7256       12019                 Cootamundra Airport  NaN     Australia  CMD   
7257       12020                 Dirranbandi Airport  NaN     Australia  DRN   
7259       12022                      Dysart Airport  NaN     Australia  DYA   
7260       12023                      Echuca Airport  NaN     Australia  ECH   
7262       12025                    Gunnedah Airport  NaN     Australia  GUH   
7263       12026                         Hay Airport  NaN     Australia  HXX   
7264       12027                    Hopetoun Airport  NaN     Australia  HTU   
7265       12028                      Kerang Airport  NaN     Australia  KRA   
7266       12029                     Kempsey Airport  NaN     Australia  KPS   
7267       12030                    Kingaroy Airport  NaN     Australia  KGY   
7269       12032                     Mareeba Airport  NaN     Australia  MRG   
7270       12033                     Ngukurr Airport  NaN     Australia  RPM   
7271       12034                   Narromine Airport  NaN     Australia  QRM   
7272       12035                  Port Pirie Airport  NaN     Australia  PPI   
7273       12036                    Smithton Airport  NaN     Australia  SIO   
7274       12037                   Snake Bay Airport  NaN     Australia  SNB   
7275       12038                     Stawell Airport  NaN     Australia  SWC   
7276       12039                  Tibooburra Airport  NaN     Australia  TYB   
7277       12040                       Tumut Airport  NaN     Australia  TUM   
7278       12041                  Wangaratta Airport  NaN     Australia  WGT   
7279       12042               Warracknabeal Airport  NaN     Australia  WKB   
7280       12043                      Warren Airport  NaN     Australia  QRR   
7283       12046                       Young Airport  NaN     Australia  NGA   
7288       12051                  Baruun Urt Airport  NaN      Mongolia  UUN   
7641       13721                Hard Bargain Airport  NaN       Bahamas   \N   
7680       14092                  Xingcheng Air Base  NaN         China  XEN   

     

Не для всех строк указано значение Timezone

In [121]:
invalid_tz = airport_raw[airport_raw['Timezone'] == '\\N']
if len(invalid_tz) > 0:
    display(pd.DataFrame(invalid_tz))
else:
    print("Нет строк, удовлетворяющих условию")

Airport ID                                           Name         City  \
6981       11743                            La Grande-4 Airport  La Grande-4   
6982       11744                              Alert Bay Airport    Alert Bay   
6983       11745         Liverpool South Shore Regional Airport    Liverpool   
6984       11747                                Nipawin Airport      Nipawin   
6985       11748  Centralia / James T. Field Memorial Aerodrome    Centralia   
...          ...                                            ...          ...   
7693       14106                            Rogachyovo Air Base       Belaya   
7694       14107                          Ulan-Ude East Airport     Ulan Ude   
7695       14108                           Krechevitsy Air Base     Novgorod   
7696       14109                    Desierto de Atacama Airport      Copiapo   
7697       14110                             Melitopol Air Base    Melitopol   

      Country IATA  ICAO   Latitude   Longitude  Altitude Timezone DST  \
6981   Canada  YAH  CYAH  53.754700  -73.675301      1005       \N  \N   
6982   Canada  YAL  CYAL  50.582199 -126.916000       240       \N  \N   
6983   Canada   \N  CYAU  44.230301  -64.856102       321       \N  \N   
6984   Canada   \N  CYBU  53.332500 -104.008003      1220       \N  \N   
6985   Canada  YCE  CYCE  43.285599  -81.508301       824       \N  \N   
...       ...  ...   ...        ...         ...       ...      ...  ..   
7693   Russia   \N  ULDA  71.616699   52.478298       272       \N  \N   
7694   Russia   \N  XIUW  51.849998  107.737999      1670       \N  \N   
7695   Russia   \N  ULLK  58.625000   31.385000        85       \N  \N   
7696    Chile  CPO  SCAT -27.261200  -70.779198       670       \N  \N   
7697  Ukraine   \N  UKDM  46.880001   35.305000         0       \N  \N   

     Tz database time zone     Type       Source  
6981                    \N  airport  OurAirports  
6982                    \N  airport  OurAirports  
6983                    \N  airport  OurAirports  
6984                    \N  airport  OurAirports  
6985                    \N  airport  OurAirports  
...                    ...      ...          ...  
7693                    \N  airport  OurAirports  
7694                    \N  airport  OurAirports  
7695                    \N  airport  OurAirports  
7696                    \N  airport  OurAirports  
7697                    \N  airport  OurAirports  

[353 rows x 14 columns]

Не для всех строк указано значение Tz database time zone

In [122]:
missing_tz_d = airport_raw[airport_raw['Tz database time zone'] == '\\N']
if len(missing_tz_d) > 0:
    display(pd.DataFrame(missing_tz_d))
else:
    print("Нет строк, удовлетворяющих условию")

Airport ID                         Name             City  \
1846        1907          Leeward Point Field       Guantanamo   
1899        1966      Tabiteuea North Airport  Tabiteuea North   
1903        1971               Rurutu Airport           Rurutu   
1908        1976                 Reao Airport             Reao   
1924        1993                  Hao Airport       Hao Island   
...          ...                          ...              ...   
7693       14106          Rogachyovo Air Base           Belaya   
7694       14107        Ulan-Ude East Airport         Ulan Ude   
7695       14108         Krechevitsy Air Base         Novgorod   
7696       14109  Desierto de Atacama Airport          Copiapo   
7697       14110           Melitopol Air Base        Melitopol   

               Country IATA  ICAO   Latitude   Longitude  Altitude Timezone  \
1846              Cuba  NBW  MUGM  19.906500  -75.207100        56       -5   
1899          Kiribati  TBF  NGTE  -1.224470  174.776001         7       12   
1903  French Polynesia  RUR  NTAR -22.434099 -151.360992        18      -10   
1908  French Polynesia  REA  NTGE -18.465900 -136.440002        12      -10   
1924  French Polynesia  HOI  NTTO -18.074800 -140.945999        10      -10   
...                ...  ...   ...        ...         ...       ...      ...   
7693            Russia   \N  ULDA  71.616699   52.478298       272       \N   
7694            Russia   \N  XIUW  51.849998  107.737999      1670       \N   
7695            Russia   \N  ULLK  58.625000   31.385000        85       \N   
7696             Chile  CPO  SCAT -27.261200  -70.779198       670       \N   
7697           Ukraine   \N  UKDM  46.880001   35.305000         0       \N   

     DST Tz database time zone     Type       Source  
1846   U                    \N  airport  OurAirports  
1899   U                    \N  airport  OurAirports  
1903   U                    \N  airport  OurAirports  
1908   U                    \N  airport  OurAirports  
1924   U                    \N  airport  OurAirports  
...   ..                   ...      ...          ...  
7693  \N                    \N  airport  OurAirports  
7694  \N                    \N  airport  OurAirports  
7695  \N                    \N  airport  OurAirports  
7696  \N                    \N  airport  OurAirports  
7697  \N                    \N  airport  OurAirports  

[1021 rows x 14 columns]

#### Несоответствие данных описанию с сайта (openflights)

В описании данных для столбца ICAO указано что там содержится либо 4-значный код, либо значение пропущено, если кода ICAO нет. Но при проверке я нашел несколько строк, где ICAO код содержит другое количество символов. Это несоответствие данных описанию. Ниже вывел такие строчки.

In [123]:
invalid_icao = airport_raw[(airport_raw['ICAO'].str.len() != 4) & (airport_raw['ICAO'] != '\\N')]
if len(invalid_icao) > 0:
    display(pd.DataFrame(invalid_icao))
else:
    print("Нет строк, удовлетворяющих условию")

Airport ID                     Name           City           Country  \
4435        5743             Kili Airport    Kili Island  Marshall Islands   
4501        5814           Utirik Airport  Utirik Island  Marshall Islands   
4765        6126  Aleknagik / New Airport      Aleknagik     United States   
4769        6134     Akutan Seaplane Base         Akutan     United States   
4770        6136     Lopez Island Airport          Lopez     United States   

     IATA ICAO   Latitude   Longitude  Altitude Timezone DST  \
4435  KIO  Q51   5.644515  169.119507         5       12   U   
4501  UTK  03N  11.222000  169.852005         4       12   U   
4765  WKK  5A8  59.282600 -158.617996        66       -9   A   
4769  KQA  KQA  54.133770 -165.778896         0       -9   A   
4770  LPS  S31  48.483898 -122.938004       209       -8   A   

     Tz database time zone     Type       Source  
4435        Pacific/Majuro  airport  OurAirports  
4501        Pacific/Majuro  airport  OurAirports  
4765     America/Anchorage  airport  OurAirports  
4769     America/Anchorage  airport  OurAirports  
4770   America/Los_Angeles  airport  OurAirports

#### Неверные данные

Для некоторых аэропортов континенты определяются неверно, это пришлось вчурную исправлять в пункте 3. Например для аэропорта, который фактически находится на одном континенте, указывалось значение Country неверно, поэтому он подсвечивался как аэропорт другого континента. И поэтому при подсвечивании аэропортов разных континентов разными цветами получалось, что аэропорт ошибочно отмечен другим цветом. Это происходило из-за неверных данных о стране аэропорта в исходном датасете.

Например так получилось с аэропортом города Орёл, который ошибочно был приписан к США. (В нём так же ошибочно указан город). Вот так это выглядело в исходном датасете:

In [124]:
airport_raw[airport_raw['Name'] == 'Oryol Yuzhny Airport']

Airport ID                  Name    City        Country IATA  ICAO  \
6862       11100  Oryol Yuzhny Airport  Oakley  United States  OEL  UUOR   

      Latitude  Longitude  Altitude Timezone DST Tz database time zone  \
6862   52.9347  36.002201       656       -5   A                    \N   

         Type       Source  
6862  airport  OurAirports

Похожие ошибки были и в некоторых других строчках из исходного датасета, соответсвующих аэропортам. Ниже представлю остальные аэропорты, которые я вручную исправил в 3 пункте:

In [125]:
airport_raw[airport_raw['Name'] == 'Gustaf III Airport']
airport_raw[airport_raw['Name'] == 'St. Helena Airport']
airport_raw[airport_raw['Name'] == 'Emporia Municipal Airport']
airport_raw[airport_raw['Name'] == 'Hunt Field']

airport_raw[airport_raw['Name'] == 'La Palma Airport']
airport_raw[airport_raw['Name'] == 'Hierro Airport']
airport_raw[airport_raw['Name'] == 'La Gomera Airport']
airport_raw[airport_raw['Name'] == 'Tenerife South Airport']
airport_raw[airport_raw['Name'] == 'Tenerife Norte Airport']
airport_raw[airport_raw['Name'] == 'Gran Canaria Airport']
airport_raw[airport_raw['Name'] == 'Fuerteventura Airport']
airport_raw[airport_raw['Name'] == 'Lanzarote Airport']

airport_raw[airport_raw['Name'] == 'Queen Beatrix International Airport']
airport_raw[airport_raw['Name'] == 'Taszár Air Base']


airport_raw[airport_raw['Name'] == 'Cyril E. King Airport']
airport_raw[airport_raw['Name'] == 'Charlotte Amalie Harbor Seaplane Base']
airport_raw[airport_raw['Name'] == 'Henry E Rohlsen Airport']

airport_raw[airport_raw['Name'] == 'Princess Juliana International Airport']
airport_raw[airport_raw['Name'] == 'Juancho E. Yrausquin Airport']
airport_raw[airport_raw['Name'] == 'Oceanside Municipal Airport']
airport_raw[airport_raw['Name'] == 'F. D. Roosevelt Airport']

Airport ID                     Name        City               Country  \
2752        2898  F. D. Roosevelt Airport  Oranjestad  Netherlands Antilles   

     IATA  ICAO  Latitude  Longitude  Altitude Timezone DST  \
2752  EUX  TNCE   17.4965 -62.979401       129       -4   U   

     Tz database time zone     Type       Source  
2752       America/Curacao  airport  OurAirports

P.S. Для некоторых аэропортов страна была указана правильно, но неправильно указывался континент. Например для островов, принадлежащих европейским странам, но территориально находящихся в Южной Америке или Африке. Такие недочеты я тоже исправлял в 3 пункте.

Ошибочно определялcя континент для страны Тринидад и Тобаго, она относится к Южной Америке

In [126]:
airport_raw.loc[airport_raw['Country'] == 'Trinidad and Tobago']

Airport ID                          Name           City  \
2755        2901    Tobago-Crown Point Airport    Scarborough   
2756        2902  Piarco International Airport  Port-of-spain   

                  Country IATA  ICAO  Latitude  Longitude  Altitude Timezone  \
2755  Trinidad and Tobago  TAB  TTCP   11.1497 -60.832199        38       -4   
2756  Trinidad and Tobago  POS  TTPP   10.5954 -61.337200        58       -4   

     DST  Tz database time zone     Type       Source  
2755   U  America/Port_of_Spain  airport  OurAirports  
2756   U  America/Port_of_Spain  airport  OurAirports

Для наглядности можно посмотреть на карту (представлена несколькими блоками ниже) с аэропортами, отмеченными разными цветами в зависимости от континента
(до ручного исправления).
Здесь представлены только аэропорты с кодом IATA, так как по условию работаем только с ними.
На этой карте наглядно видно что для некоторых аэропортов значение страны указано неверно.

In [127]:
patch = 'https://raw.githubusercontent.com/jpatokal/openflights/master/data/airports.dat'
airport_raw = pd.read_csv(patch, sep = ',', engine = 'python',
           header = None,
           names = ['Airport ID', 'Name', 'City', 'Country', 'IATA', 'ICAO', 'Latitude', 'Longitude', 'Altitude', 'Timezone', 'DST', 'Tz database time zone', 'Type', 'Source'])
airport_raw = airport_raw.drop(airport_raw[airport_raw['IATA'] == '\\N'].index)
airport_raw.head()

Airport ID                                         Name          City  \
0           1                               Goroka Airport        Goroka   
1           2                               Madang Airport        Madang   
2           3                 Mount Hagen Kagamuga Airport   Mount Hagen   
3           4                               Nadzab Airport        Nadzab   
4           5  Port Moresby Jacksons International Airport  Port Moresby   

            Country IATA  ICAO  Latitude   Longitude  Altitude Timezone DST  \
0  Papua New Guinea  GKA  AYGA -6.081690  145.391998      5282       10   U   
1  Papua New Guinea  MAG  AYMD -5.207080  145.789001        20       10   U   
2  Papua New Guinea  HGU  AYMH -5.826790  144.296005      5388       10   U   
3  Papua New Guinea  LAE  AYNZ -6.569803  146.725977       239       10   U   
4  Papua New Guinea  POM  AYPY -9.443380  147.220001       146       10   U   

  Tz database time zone     Type       Source  
0  Pacific/Port_Moresby  airport  OurAirports  
1  Pacific/Port_Moresby  airport  OurAirports  
2  Pacific/Port_Moresby  airport  OurAirports  
3  Pacific/Port_Moresby  airport  OurAirports  
4  Pacific/Port_Moresby  airport  OurAirports

In [128]:
#pip install folium

In [129]:
#pip install pycountry-convert

In [130]:
import folium
import pycountry_convert as pc

In [131]:
def get_continent(country):
    extra_countries = {
        "Cote d'Ivoire": 'Africa', 
        'Congo (Kinshasa)': 'Africa', 
        'Congo (Brazzaville)': 'Africa',
        'Saint Helena' :'Africa',
        'Reunion' : 'Africa',
        'Midway Islands':'North America',
        'Antarctica': 'Antarctica',
        'Virgin Islands':'South America',
        'Netherlands Antilles': 'South America',
        'Burma': 'Asia',
        'East Timor': 'Asia',
        'Wake Island':'Australia/Oceania',
        'Western Sahara':'Africa',
        'Johnston Atoll':'North America'
    }
    try:
        country_code = pc.country_name_to_country_alpha2(country)
        continent_code = pc.country_alpha2_to_continent_code(country_code)
        continent = pc.convert_continent_code_to_continent_name(continent_code)
        if continent == 'Oceania':
            continent = 'Australia/Oceania'
        return continent
    except:
        if country in extra_countries:
            return extra_countries[country]
        else:
            return 'Unknown'

In [132]:
airport_raw['Continent'] = airport_raw['Country'].apply(get_continent)

In [133]:
world_map_with_menu = folium.Map(location=[0, 0], zoom_start=2)

# Создаем группы
sa_group = folium.FeatureGroup(name='South America')
na_group = folium.FeatureGroup(name='North America')
eu_group = folium.FeatureGroup(name='Europe')
asia_group = folium.FeatureGroup(name='Asia')
afr_group = folium.FeatureGroup(name='Africa')
aus_group = folium.FeatureGroup(name='Australia')
ant_group = folium.FeatureGroup(name='Antarctica')

# Добавляем на карту аэропорты для каждого континента
south_america_airports = airport_raw[airport_raw['Continent'] == 'South America']
for i, row in south_america_airports.iterrows():
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=3,
                        color='green',
                        fill=True,
                        fill_color='green',
                        fill_opacity=1,
                        popup=row['Name']).add_to(sa_group)

na_airports = airport_raw[airport_raw['Continent'] == 'North America']
for i, row in na_airports.iterrows():
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=3,
                        color='purple',
                        fill=True,
                        fill_color='purple',
                        fill_opacity=1,
                        popup=row['Name']).add_to(na_group)
    
europe_airports = airport_raw[airport_raw['Continent'] == 'Europe']
for i, row in europe_airports.iterrows():
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=3,
                        color='orange',
                        fill=True,
                        fill_color='orange',
                        fill_opacity=1,
                        popup=row['Name']).add_to(eu_group)
    
africa_airports = airport_raw[airport_raw['Continent'] == 'Africa']
for i, row in africa_airports.iterrows():
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=3,
                        color='red',
                        fill=True,
                        fill_color='red',
                        fill_opacity=1,
                        popup=row['Name']).add_to(afr_group)
    
asia_airports = airport_raw[airport_raw['Continent'] == 'Asia']
for i, row in asia_airports.iterrows():
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=3,
                        color='blue',
                        fill=True,
                        fill_color='blue',
                        fill_opacity=1,
                        popup=row['Name']).add_to(asia_group)
    
aust_airports = airport_raw[airport_raw['Continent'].isin(['Australia/Oceania'])]
for i, row in aust_airports.iterrows():
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=3,
                        color='',
                        fill=True,
                        fill_color='cadetblue',
                        fill_opacity=1,
                        popup=row['Name']).add_to(aus_group)
    
antarctica_airports = airport_raw[airport_raw['Continent'].isin(['Antarctica'])]
for i, row in antarctica_airports.iterrows():
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=3,
                        color='yellow',
                        fill=True,
                        fill_color='yellow',
                        fill_opacity=1,
                        popup=row['Name']).add_to(ant_group)


sa_group.add_to(world_map_with_menu)
na_group.add_to(world_map_with_menu)
eu_group.add_to(world_map_with_menu)
asia_group.add_to(world_map_with_menu)
afr_group.add_to(world_map_with_menu)
aus_group.add_to(world_map_with_menu)
ant_group.add_to(world_map_with_menu)

folium.LayerControl().add_to(world_map_with_menu)


world_map_with_menu

В исходном датасете были некоторые территории для которых не определялся континент. Их пришлось добавлять в функцию вручную. (Например это спорные территории)
"Cote d'Ivoire": 'Africa', 
        'Congo (Kinshasa)': 'Africa', 
        'Congo (Brazzaville)': 'Africa',
        'Saint Helena' :'Africa',
        'Reunion' : 'Africa',
        'Midway Islands':'North America',
        'Antarctica': 'Antarctica',
        'Virgin Islands':'South America',
        'Netherlands Antilles': 'South America',
        'Burma': 'Asia',
        'East Timor': 'Asia',
        'Wake Island':'Australia/Oceania',
        'Western Sahara':'Africa',
        'Johnston Atoll':'North America'

### Теперь ищем ошибки в исходном датасете rout_raw

In [134]:
patch_1 = 'https://raw.githubusercontent.com/jpatokal/openflights/master/data/routes.dat'
rout_raw = pd.read_csv(patch_1, sep = ',', engine = 'python',
           header = None,
           names = ['Airline', 'Airline ID', 'Source airport', 'Source airport ID', 'Destination airport', 'Destination airport ID', 'Codeshare', 'Stops', 'Equipment'])
rout_raw

Airline Airline ID Source airport Source airport ID Destination airport  \
0          2B        410            AER              2965                 KZN   
1          2B        410            ASF              2966                 KZN   
2          2B        410            ASF              2966                 MRV   
3          2B        410            CEK              2968                 KZN   
4          2B        410            CEK              2968                 OVB   
...       ...        ...            ...               ...                 ...   
67658      ZL       4178            WYA              6334                 ADL   
67659      ZM      19016            DME              4029                 FRU   
67660      ZM      19016            FRU              2912                 DME   
67661      ZM      19016            FRU              2912                 OSS   
67662      ZM      19016            OSS              2913                 FRU   

      Destination airport ID Codeshare  Stops Equipment  
0                       2990       NaN      0       CR2  
1                       2990       NaN      0       CR2  
2                       2962       NaN      0       CR2  
3                       2990       NaN      0       CR2  
4                       4078       NaN      0       CR2  
...                      ...       ...    ...       ...  
67658                   3341       NaN      0       SF3  
67659                   2912       NaN      0       734  
67660                   4029       NaN      0       734  
67661                   2913       NaN      0       734  
67662                   2912       NaN      0       734  

[67663 rows x 9 columns]

#### Пропущенные данные

Для некоторых строк пропущены данные в столбце Airline ID

In [135]:
df_filtered_ID = rout_raw[rout_raw['Airline ID'] == '\\N']

df_filtered_ID

Airline Airline ID Source airport Source airport ID Destination airport  \
312        3H         \N            AKV              5506                 YIK   
313        3H         \N            AKV              5506                 YPX   
314        3H         \N            XGR              5512                 YVP   
315        3H         \N            YGL                62                 YGW   
316        3H         \N            YGL                62                 YPX   
...       ...        ...            ...               ...                 ...   
66596      ZD         \N            DZA               915                 MJN   
66597      ZD         \N            DZA               915                 NOS   
66598      ZD         \N            HAH               912                 DZA   
66599      ZD         \N            MJN               929                 DZA   
66600      ZD         \N            NOS               930                 DZA   

      Destination airport ID Codeshare  Stops Equipment  
312                     5504       NaN      0       DH8  
313                     6727       NaN      0       DH8  
314                      154       NaN      0   DHT BET  
315                     5496       NaN      0       DHT  
316                     6727       NaN      0       73M  
...                      ...       ...    ...       ...  
66596                    929       NaN      0       AT7  
66597                    930       NaN      0       AT7  
66598                    915       NaN      0       AT7  
66599                    915       NaN      0       AT7  
66600                    915       NaN      0       AT7  

[479 rows x 9 columns]

Для некоторых строк пропущены данные в столбце Source Airport ID

In [136]:
df_filtered_ID = rout_raw[rout_raw['Source airport ID'] == '\\N']

df_filtered_ID

Airline Airline ID Source airport Source airport ID Destination airport  \
38         2B        410            TGK                \N                 DME   
54         2G       1654            KCK                \N                 IKT   
1163       4O      17885            PQM                \N                 MEX   
2113       5Z      18946            PBZ                \N                 CPT   
2114       5Z      18946            PBZ                \N                 JNB   
...       ...        ...            ...               ...                 ...   
66353      Z8        603            ORU                \N                 SRZ   
67468      ZI         21            MLH                \N                 ALG   
67469      ZI         21            MLH                \N                 CZL   
67470      ZI         21            MLH                \N                 ORN   
67471      ZI         21            MLH                \N                 QSF   

      Destination airport ID Codeshare  Stops Equipment  
38                      4029       NaN      0       CR2  
54                      2937       NaN      0       AN4  
1163                    1824       NaN      0       SU9  
2113                     797       NaN      0       BEH  
2114                     813       NaN      0       BEH  
...                      ...       ...    ...       ...  
66353                   4247       NaN      0       SWM  
67468                    210       NaN      0       320  
67469                    221       NaN      0       320  
67470                    231       NaN      0       319  
67471                   6492       NaN      0       320  

[220 rows x 9 columns]

Для некоторых строк пропущены данные в столбце Destination Airport ID

In [137]:
df_filtered_ID = rout_raw[rout_raw['Destination airport ID'] == '\\N']

df_filtered_ID

Airline Airline ID Source airport Source airport ID Destination airport  \
7          2B        410            DME              4029                 TGK   
48         2G       1654            IKT              2937                 KCK   
1136       4O      17885            MEX              1824                 PQM   
2108       5Z      18946            CPT               797                 PBZ   
2120       6E       2850            AMD              2994                 HYD   
...       ...        ...            ...               ...                 ...   
66361      Z8        603            SRZ              4247                 ORU   
67443      ZI         21            ALG               210                 MLH   
67455      ZI         21            CZL               221                 MLH   
67483      ZI         21            ORN               231                 MLH   
67502      ZI         21            QSF              6492                 MLH   

      Destination airport ID Codeshare  Stops Equipment  
7                         \N       NaN      0       CR2  
48                        \N       NaN      0       AN4  
1136                      \N       NaN      0       SU9  
2108                      \N       NaN      0       BEH  
2120                      \N       NaN      0       320  
...                      ...       ...    ...       ...  
66361                     \N       NaN      0       SWM  
67443                     \N       NaN      0       320  
67455                     \N       NaN      0       320  
67483                     \N       NaN      0       319  
67502                     \N       NaN      0       320  

[221 rows x 9 columns]

Таким образом для второго датасета найден один тип ошибок: пропущенные данные